[Seedstars Dataset](https://docs.google.com/spreadsheets/d/1-obbie4i408IPnYzsSePyGI5cWkNfHPd/edit#gid=1896756205)

In [1]:
!pip install folium

# Loading the data

In [2]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

In [3]:
seedstars = pd.read_csv('seedstars.csv')
seedstars.shape

(4255, 90)

In [4]:
seedstars.head()

company_id  ... age at the time of final funding (in months)
0           1  ...                                          NaN
1           2  ...                                          NaN
2           3  ...                                          NaN
3           4  ...                                          NaN
4           5  ...                                          NaN

[5 rows x 90 columns]

In [5]:
seedstars.set_index('company_id', inplace= True)

In [6]:
seedstars.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4255 entries, 1 to 4255
Data columns (total 89 columns):
 #   Column                                                                                  Non-Null Count  Dtype  
---  ------                                                                                  --------------  -----  
 0   event_name                                                                              4237 non-null   object 
 1   country                                                                                 4242 non-null   object 
 2   industry                                                                                4133 non-null   object 
 3   business_stage                                                                          3560 non-null   object 
 4   incorporated                                                                            3561 non-null   float64
 5   incorporation_date                                                   

# Data Cleaning & Features Eng

### Bunch of Missing values?

We notice a many entirely null columns. We can start by dropping these. 

In [7]:
seedstars= seedstars.dropna(axis=1, how='all')

In [8]:
percent_missing = seedstars.isnull().sum() * 100 / len(seedstars)
missing_startups_data = pd.DataFrame({'column_name': seedstars.columns,
                                 'percent_missing': percent_missing})
missing_startups_data[percent_missing > 80]

column_name  percent_missing
date_first_sale                                                                       date_first_sale        83.666275
birthdate_1                                                                               birthdate_1        88.108108
Age of the entrepreneur 1                                                   Age of the entrepreneur 1        88.108108
birthdate_2                                                                               birthdate_2        93.137485
Age of the entrepreneur 2                                                   Age of the entrepreneur 2        93.137485
city_2                                                                                         city_2        86.815511
country_2                                                                                   country_2        86.768508
Latest annualized revenues USD                                         Latest annualized revenues USD        98.824912
CAGR since incorporation                                                     CAGR since incorporation        99.130435
# of employees - normalise it or average it + a...  # of employees - normalise it or average it + ...        92.432432
Date we collected the information                                   Date we collected the information        92.385429
FUNDING AFTER THE EVENT                                                       FUNDING AFTER THE EVENT        89.917744
Funding after the event?                                                     Funding after the event?        89.917744
FUNDING - ALL FROM 3RD PARTY                                             FUNDING - ALL FROM 3RD PARTY        89.917744

In [9]:
# Drop columns more than 80% missing except 'date_first_sale'
seedstars.drop(['# of employees - normalise it or average it + add the date when the data was collected', 'Latest annualized revenues USD', 'CAGR since incorporation', 'Date we collected the information', 'FUNDING AFTER THE EVENT', 'Funding after the event?', 'FUNDING - ALL FROM 3RD PARTY'], axis=1, inplace=True)

### Incorporation year

In [10]:
seedstars['date_created'].unique()

array(['2018-04', nan, '2019-06', '2018-06', '2018-10', '2019-07',
       '2018-08', '2019-10', '2019-11', '2018-05', '2019-08', '2018-12',
       '2018-07', '2020-02', '2018-11', '2019-09', '2018-09', '2017-10',
       '2019-05', '2020-01', '2018-9', '2019-04', '2020-03', '2017-11',
       '2016-12', '2019-12',
       "SSW15 _ Merchandiser' (by Codefish) _ Seedstars Beirut _ Investment Summary",
       'SSW15 _ GoodMealHunting _ Seedstars Manila _ Investment Summary',
       '2016-11',
       "SSW15 _ U.M.S 'Queen' _ Seedstars Yangon _ Investment Summary",
       '2018-01', '2017-05', '2017-08',
       'SSW15 _ Bulletinboard _ Seedstars Jakarta _ Investment Summary',
       'SSW15 _ Flip _ Seedstars Jakarta _ Investment Summary',
       'SSW15 _ Ecoisme _ Seedstars Kiev _ Investment Summary', '2017-09',
       'SSW15 _ PICVPIC LTD _ Seedstars Kiev _ Investment Summary',
       'SSW15 _ Modisar Net _ Seedstars Gaborone _ Investment Summary',
       '2017-12', '2016-07', '2019-01'], dty

In [11]:
seedstars['incorporation_date'].isnull().sum()* 100 / len(seedstars['incorporation_date'])

13.27849588719154

In [12]:
seedstars[['date_created', 'incorporation_date']]

date_created incorporation_date
company_id                                
1               2018-04            2017-09
2                   NaN            2017-02
3                   NaN            2015-11
4                   NaN            2016-03
5                   NaN            2015-05
...                 ...                ...
4251            2016-07                NaN
4252            2018-06            2017-01
4253                NaN                NaN
4254            2018-10            2017-11
4255            2019-01                NaN

[4255 rows x 2 columns]

if if `incorporation_date` is missing, replace with `'date_created'` (if it's a date not a descriptive text).
Then drop `'date_created'`

In [13]:
seedstars.incorporation_date.fillna(seedstars.date_created, inplace=True)

In [14]:
def getYear(mydate):
  mydate = str(mydate)
  if mydate[0].isnumeric(): # Format 'yyyy-mm'
    return mydate[:4]
  elif mydate[0].isalpha(): # non date text
    return None
seedstars['incorporation_date'] = seedstars['incorporation_date'].apply(lambda x: getYear(x))

In [15]:
seedstars['incorporation_date'].isnull().sum()* 100 / len(seedstars['incorporation_date'])

12.784958871915393

Decreased by < 1%

We can replace the null values from the year of the date_first_sale? (We can also try date_first_sale - 1)

In [16]:
seedstars['date_first_sale'].isnull().sum()* 100 / len(seedstars['date_first_sale'])

83.6662749706228

In [17]:
seedstars['date_first_sale'] = seedstars['date_first_sale'].apply(lambda x: x if x != x else str(x).split('-')[0])
seedstars['date_first_sale'].isnull().sum()

3560

In [18]:
seedstars.incorporation_date.fillna(seedstars.date_first_sale, inplace=True)

In [19]:
seedstars['incorporation_date'].isnull().sum()* 100 / len(seedstars['incorporation_date'])

9.283196239717979

Missing values decreased by 3%

We can fill the rest with the mode:

In [20]:
seedstars['incorporation_date'].mode()

0    2017
dtype: object

In [21]:
seedstars.incorporation_date.fillna(seedstars['incorporation_date'].mode()[0], inplace=True)

In [22]:
seedstars.drop('date_first_sale', axis=1, inplace=True)

### Age ?

What's `'Age today'` ? To keep or to drop ?

In [23]:
seedstars[['Age of the entrepreneur 0', 'Age of the entrepreneur 1', 'Age of the entrepreneur 2', 'Age today']].head()

Age of the entrepreneur 0  ...  Age today
company_id                             ...           
1                                31.0  ...       36.0
2                                43.0  ...       43.0
3                                 NaN  ...       58.0
4                                 NaN  ...       54.0
5                                 NaN  ...       64.0

[5 rows x 4 columns]

In [24]:
seedstars.drop('Age today', axis=1, inplace=True)

### Founders

Keep the data of the first Entrepreneur 0, dropping 1 and 2 since they have less data.

In [25]:
seedstars.drop(['role_1', 'gender_1', 'birthdate_1', 'Age of the entrepreneur 1', 'city_1', 'country_1', 
                'role_2', 'gender_2', 'birthdate_2', 'Age of the entrepreneur 2', 'city_2','country_2'], axis=1, inplace=True)

### Team members

What's the difference between `'Number of team members'` and 'number_employees'

In [26]:
seedstars[['Number of team members', 'number_employees']]

Number of team members  number_employees
company_id                                          
1                              4.0               1.0
2                              7.0              10.0
3                              3.0               6.0
4                              3.0               5.0
5                              2.0               5.0
...                            ...               ...
4251                           4.0               5.0
4252                           1.0               2.0
4253                           NaN               NaN
4254                           8.0               5.0
4255                           NaN               NaN

[4255 rows x 2 columns]

### Website activity

Convert column `WEBSITE DEAD?` => 0 or 1

In [27]:
seedstars['WEBSITE DEAD?'] = seedstars['WEBSITE DEAD?'].apply(lambda x: 1 if 'ALIVE' else 0)

### Funding

In [28]:
seedstars['NEW DATA?'].describe()

count     1650
unique       1
top        YES
freq      1650
Name: NEW DATA?, dtype: object

In [29]:
seedstars.drop('NEW DATA?', axis=1, inplace=True)

In [30]:
seedstars['event_name']

company_id
1            Seedstars Tashkent
2            Seedstars Shanghai
3              Seedstars Maputo
4       Seedstars Vicente Lopez
5               Seedstars Dhaka
                 ...           
4251       Seedstars Santa Cruz
4252            Seedstars Amman
4253                        NaN
4254              Seedstars KSA
4255                        NaN
Name: event_name, Length: 4255, dtype: object

In [31]:
seedstars.drop('event_name', axis=1, inplace=True)

## Country

In [32]:
seedstars['country'].unique()

array(['Uzbekistan', 'China', 'Mozambique', 'Argentina', 'Bangladesh',
       'Indonesia', 'Iran', 'Australia', 'Kazakhstan', 'Malaysia',
       'Vietnam', 'Guatemala', 'Philippines', 'Poland', 'Nigeria',
       'Rwanda', 'Lebanon', 'Uganda', 'Ukraine', 'Senegal', 'Myanmar',
       'Jordan', 'Armenia', 'Malawi', 'South Africa', 'Egypt',
       'Singapore', 'India', 'Ecuador', 'Peru', 'Hong Kong', 'Estonia',
       'Iraq', 'Uruguay', 'Ethiopia', 'Kenya', 'Taiwan', 'Czech Republic',
       'United States', 'Colombia', 'Bulgaria', 'Serbia', 'Panama',
       'Palestine', 'Thailand', 'Brazil', 'Botswana', 'Pakistan',
       'Algeria', 'Gambia', "Cote d'Ivoire", 'Mali', 'Zimbabwe',
       'Tunisia', 'Democratic Republic of Congo', 'Ghana', 'Tanzania',
       'Switzerland', 'Morocco', 'Cameroon', 'Sierra Leone', 'Chile',
       'Latvia', 'Mexico', 'Turkey', 'Russia', 'Bahrain', 'Saudi Arabia',
       'Sri Lanka', 'United Arab Emirates', 'Bolivia', 'Azerbaijan',
       'South Korea', 'Libya', 

In [33]:
seedstars[seedstars['country'].isnull()]

country           industry  ...  Total Funding  WEBSITE DEAD?
company_id                             ...                              
1533           NaN                NaN  ...            NaN              1
1618           NaN                NaN  ...            NaN              1
1678           NaN  Consumer Products  ...            NaN              1
1713           NaN              Other  ...            NaN              1
1720           NaN                NaN  ...            NaN              1
1922           NaN  Health / Wellness  ...  $3.000.000,00              1
2412           NaN                NaN  ...            NaN              1
2466           NaN                NaN  ...            NaN              1
2804           NaN                NaN  ...            NaN              1
2927           NaN                NaN  ...            NaN              1
2962           NaN                NaN  ...            NaN              1
3197           NaN                NaN  ...            NaN              1
3246           NaN                NaN  ...            NaN              1

[13 rows x 50 columns]

In [34]:
to_drop = seedstars[seedstars['country'].isnull() & (seedstars['industry'].isnull())].index
seedstars.drop(index=to_drop, inplace=True)

In [35]:
seedstars[seedstars['country'].isnull()]

country           industry  ...  Total Funding  WEBSITE DEAD?
company_id                             ...                              
1678           NaN  Consumer Products  ...            NaN              1
1713           NaN              Other  ...            NaN              1
1922           NaN  Health / Wellness  ...  $3.000.000,00              1

[3 rows x 50 columns]

In [36]:
seedstars['country'].fillna(seedstars['country_0'], inplace=True)

In [37]:
seedstars[seedstars['country'].isnull()]

country industry  ... Total Funding  WEBSITE DEAD?
company_id                   ...                             
1713           NaN    Other  ...           NaN              1

[1 rows x 50 columns]

In [38]:
to_drop = seedstars[seedstars['country'].isnull()].index

In [39]:
seedstars.drop(index= to_drop, inplace=True)

We want to visualize a map of the countries. 
<br/>
First, we will use [Nomatim Open Street Map Search API](https://nominatim.openstreetmap.org/ui/search.html) to get the coordinates of the countries:

In [40]:
import requests

def get_center_coord(country):
    url = '{0}{1}{2}'.format('http://nominatim.openstreetmap.org/search?country=',
                             country,
                             '&format=json&polygon=0')
    try:
      response = requests.get(url).json()[0]
    except: # We'll deal with this manually below
      return None

    # parse response to list
    lst = [response.get(key) for key in ['lat','lon']]
    center_coord = [float(i) for i in lst]
    
    return center_coord

We check the unique countries in our dataset because no need to make duplicate calls to the API.

In [41]:
unique_countries = seedstars['country'].unique()

In [42]:
import numpy as np
def get_coord(country):
  center = get_center_coord(country.lower())
  if center is None:
    if country == 'Hong Kong':
      return [22.2793278, 114.1628131]
    elif country == 'Palestine':
      return [31.94696655, 35.27386547291496]
    elif country == 'Puerto Rico':
      return [18.2214149, -66.41328179513847]
    else: 
      return country
  else:
    return center

In [43]:
# This Nominatim API call will take ~ 1mn
countries_coord = [get_coord(x) for x in unique_countries]

In [47]:
coordinates = pd.DataFrame(columns = ['country', 'coordinates'])
coordinates['country'] = seedstars['country'].unique()
coordinates['coordinates'] = countries_coord

In [48]:
coordinates.head()

country                 coordinates
0  Uzbekistan      [41.32373, 63.9528098]
1       China     [35.000074, 104.999927]
2  Mozambique    [-19.302233, 34.9144977]
3   Argentina  [-34.9964963, -64.9672817]
4  Bangladesh    [24.4768783, 90.2932426]

In [49]:
coordinates['lat'] = coordinates['coordinates'].apply(lambda x: x[0])
coordinates['lon'] = coordinates['coordinates'].apply(lambda x: x[1])

In [50]:
coordinates.head()

country                 coordinates        lat         lon
0  Uzbekistan      [41.32373, 63.9528098]  41.323730   63.952810
1       China     [35.000074, 104.999927]  35.000074  104.999927
2  Mozambique    [-19.302233, 34.9144977] -19.302233   34.914498
3   Argentina  [-34.9964963, -64.9672817] -34.996496  -64.967282
4  Bangladesh    [24.4768783, 90.2932426]  24.476878   90.293243

In [51]:
# Map each coordinate to the corressponding country in our dataset
seedstars = pd.merge(seedstars, coordinates[['country', 'lat', 'lon']], how='inner', on='country')

In [52]:
# Create a world map to show distributions of startups 
import folium
from folium.plugins import MarkerCluster
# Empty map
world_map= folium.Map(tiles="cartodbpositron")
marker_cluster = MarkerCluster().add_to(world_map)
# For each coordinate, create circlemarker of startups
for i in range(len(seedstars)):
        lat = seedstars.iloc[i]['lat']
        lon = seedstars.iloc[i]['lon']
        radius=5
        popup_text = """Country : {}<br>"""
        popup_text = popup_text.format(seedstars.iloc[i]['country'])

        folium.CircleMarker(location = [lat, lon], radius=radius, popup= popup_text, fill =True).add_to(marker_cluster)
#show the map
world_map

In [71]:
seedstars.columns

Index(['country', 'industry', 'business_stage', 'incorporated',
       'incorporation_date', 'Number of team members',
       'revenue_model_commission', 'revenue_model_product',
       'revenue_model_on-demand', 'revenue_model_subscription',
       'revenue_model_freemium', 'revenue_model_advertising',
       'revenue_model_licensing', 'customer_type - B-to-B-to-C',
       'customer_type - B-to-B', 'customer_type - B-to-C',
       'customer_type - B-to-G', 'customer_interaction - web',
       'customer_interaction - mobile', 'customer_interaction - physical',
       'accelerator', 'amount_to_raise', 'status_of_funding',
       'funding at the time of application', 'number_employees',
       'revenue_1month', 'revenue_2month', 'revenue_3month', 'users_1month',
       'users_2month', 'users_3month', 'paying_users_1month',
       'paying_users_2month', 'paying_users_3month',
       'number_transactions_1month', 'number_transactions_2month',
       'number_transactions_3month', 'burn_rate

ToDo next:
Look into columns about : <br/> 

*   'revenue_model_'
*   'customer_type'
*   'customer_interaction'
*   'funding'
*   'users_'
*   'number_transactions'